In [ ]:
# This cell is added by sphinx-gallery
# It can be customized to whatever you like
%matplotlib inline

# Introducing tensor networks for quantum practitioners

If you are well-versed in the topics of [quantum
computing](https://pennylane.ai/qml/what-is-quantum-computing) or
quantum information, chances are you have heard (quite often) about
tensor networks. In fact, tensor networks are a widely used tool with
applications ranging across physics, math, and computer science.

Part of the excitement surrounding tensor networks is due to their
ability to represent complex data efficiently, which allows for---among
other things---fast classical simulations. In addition, the diagrammatic
language accompanying tensor networks makes working with them intuitive
and suitable for describing a vast range of mathematical concepts,
including quantum circuits.

![](../_static/demo_thumbnails/opengraph_demo_thumbnails/OGthumbnail_tensor_network_basics.png){.align-center
width="70.0%"}

The `first part of this demo <part_one>`{.interpreted-text role="ref"}
introduces the basic tensor network notions and definitions to quantum
practitioners who are familiar with quantum computing but new to tensor
networks.

Then, building on this introduction, in the
`second part <part_two>`{.interpreted-text role="ref"} we explore topics
aimed at more seasoned readers. Check this section out if you want to
understand how tensor networks and quantum circuits are related!

Without further ado, let's dive right in! 🤓📚

## A first glimpse into the tensor networks world {#part_one}

### From matrices to tensors

First, we start by answering the question: **what is a tensor?**

A common and intuitive way of thinking about tensors is as
generalizations of vectors and matrices. That is, we can think of them
as multidimensional arrays---i.e., multidimensional maps that are linear
with respect to every parameter. A tensor of dimensions
$d_1 \times d_2 \times \ldots \times d_r$ can be expressed as

$$T_{i_1, i_2, \ldots, i_r} \in \mathbb{C}^{d_1 \times d_2 \times \ldots \times d_r},$$

where each $i_n$ is an **index** of dimension $d_n$ and the number of
indices $r$ is known as the **rank** of the tensor. We say $T$ is a
rank-$r$ tensor. We will denote the $(i_1, i_2, \ldots, i_r)$-th entry
of the tensor $T$ as $(T)_{i_1, i_2, \ldots, i_r}$ --- this is a single
number.

For example, a scalar $s$ is a rank-0 tensor, a vector $v_i$ is a rank-1
tensor, and a matrix $G_{j,i}$ is a rank-2 tensor.

::: note
::: title
Note
:::

Some authors refer to the indices $i_n$ as the \"dimensions of the
tensor\". In this demo, however, the term **dimension** refers to the
range of integer values $d_n$ that each index $i_n$ can take, namely
$i_n \in \{1, \ldots, d_n\}$.
:::

A beautiful and powerful tool accompanying tensors is their graphical
language representation. The diagram of a tensor is simply a geometric
shape with a leg sticking out of it for every index in the tensor. For
example,

![](../_static/demonstration_assets/tn_basics/01-tensor.png){.align-center
width="40.0%"}

We can apply this same idea to represent a scalar, a vector, and a
matrix:

![](../_static/demonstration_assets/tn_basics/02-tensors.png){.align-center
width="40.0%"}

Does the last diagram seem familiar? It is because this is the
representation of a single-qubit gate! Later in this demo, we will study
the relation between quantum circuits and tensor networks.

When working within the quantum computing notation, we adopt the
convention that drawing the leg of a quantum state (i.e., a vector) to
the right corresponds to a ket, i.e., a vector living in the Hilbert
space, while drawing the legs to the left means they are a bra vector,
i.e., living in the dual space.

![](../_static/demonstration_assets/tn_basics/03-braket.png){.align-center
width="55.0%"}

::: note
::: title
Note
:::

The diagrammatic representation of tensors is rooted in category theory,
which equips the diagrams with all the relevant information so they can
be used in proofs and formal reasoning! 💡
:::

Creating a tensor in code is straightforward, and chances are you have
already created one yourself. Using `numpy`, all we have to do is create
a `np.array` of the desired rank. For instance, we can start by creating
a rank-1 tensor (a vector).


In [ ]:
import numpy as np

tensor_rank1 = np.array([1, 2, 3, 4])
print("rank: ", tensor_rank1.ndim)
print("dimensions: ", tensor_rank1.shape)

Then, we can use this to construct a rank-2 tensor (a matrix).


In [ ]:
tensor_rank2 = np.array([tensor_rank1, tensor_rank1, tensor_rank1])
print("rank: ", tensor_rank2.ndim)
print("dimensions: ", tensor_rank2.shape)

As you might have guessed, we can repeat this procedure to create a
rank-3 tensor.


In [ ]:
tensor_rank3 = np.array([tensor_rank2, tensor_rank2])
print("rank: ", tensor_rank3.ndim)
print("dimensions: ", tensor_rank3.shape)
print("Rank-3 tensor: \n", tensor_rank3)

We can create a tensor of arbitrary rank following a similar procedure.
This recursive approach illustrates how a rank-$r$ tensor can be seen as
consisting of nested rank-$(r-1)$ tensors. This translates into code as
adding another level to the nested bracket structure:
`[tensor_rank_r-1]`.

Now that we understand what a tensor is---and even know how to code
one---let us look at how to combine them to create a tensor network.


# From matrix multiplication to tensor contractions

Matrix-matrix and matrix-vector multiplications are familiar operations
within the context of quantum computing. We can now study these
operations through the lens of the tensor notation introduced above.
First, a matrix $G$ and a vector $v$ can be multiplied such that the
$j$-th element of the resulting vector is

$$(w)_j = \sum_i (G)_{j, i} (v)_i .$$

![](../_static/demonstration_assets/tn_basics/04-matrix-vector.png){.align-center
width="55.0%"}

::: note
::: title
Note
:::

Recall we are adopting the convention of drawing a ket vector with its
leg pointing right, as done in quantum circuits. In turn, this means the
\"input\" index of a matrix---its column index---points towards the left
while the \"output\" index---its row index---points to the right. In the
example above for $G_{j, i}$, the input and output indices are index $i$
and index $j$, respectively.
:::

We see that summing over the shared index $i$ is equivalent to
**contracting** the corresponding legs from the matrix and vector
diagrams. As expected, the result of this multiplication is another
rank-1 tensor with dangling leg $j$. Similarly, we can look at the
matrix-matrix multiplication $G^3 = G^2 \cdot G^1$ and its $(k,i)$-th
element is given by

$$(G^3)_{k,i} = \sum_j (G^2)_{k,j} (G^1)_{j,i} .$$

![](../_static/demonstration_assets/tn_basics/05-matrix-matrix.png){.align-center
width="55.0%"}

Here, the resulting tensor has two dangling indices, $i$ and $k$,
defining a matrix, as expected!

We can now generalize this concept to tensors, and consequently, to more
than two legs being contracted. For example, let us look at three
tensors $A_{i,j,k}$, $B_{j,l,m}$, and $C_{k,m,n}$. To contract them, all
we need to do is to sum over repeated indices ($j$, $k$, $m$). To obtain
the $(i,l,n)$-th element of the resulting tensor $D$, we perform this
contraction by summing over $j, k, m$

$$(D)_{i,l,n} =  \sum_{j,k,m} (A)_{i,j,k} (B)_{j,l,m} (C)_{k,m,n} .$$

Using the tensor product $\otimes$ between the 3 tensors and summing
over the repeated indices we can obtain a similar expression for the
full tensor $D$

$$D_{i,l,n} = \sum_{j,k,m} A_{i,j,k} \otimes B_{j,l,m} \otimes C_{k,m,n}.$$

The resulting rank-3 tensor consists of the remaining open legs from the
initial tensors $(i,l,n)$. The first equation involving only scalars is
the more widely used expression for the contraction operation, and thus,
we will use it throughout this demo unless otherwise stated. The
diagrammatic representation of this contraction is obtained by
connecting all the legs with the same indices.

![](../_static/demonstration_assets/tn_basics/06-tensor-tensor.png){.align-center
width="55.0%"}

With the above contraction, we have formed a network of tensors, i.e., a
**tensor network**!

::: note
::: title
Note
:::

A common question arising when drawing a tensor is: \"What is the
correct order to draw the indices?\" For instance, in the figure above,
we have adopted the convention that a tensor $A_{i,j,k}$ corresponds to
a diagram with the first leg ($i$) pointing left, the second leg ($j$)
pointing upwards, and the third leg ($k$) pointing right, and similarly
for the other two tensors. However, this need not be the case. We could
have defined the first leg to be the one pointing upwards, for example.
Based on the use case, and the user, some conventions might seem more
natural than others. The only important thing to keep in mind is to be
consistent. In other words, once we choose a convention for the order,
we should apply it to all the tensors to avoid contracting the wrong
indices.
:::

In our code, we can perform a tensor contraction using the `numpy`
function `np.einsum`. To do so, we can start by creating the 3 tensors
to be contracted by reshaping a 1D array (created using `np.arange`)
into rank-3 tensors of the correct dimensions.


In [ ]:
# Create the individual rank-3 tensors
A = np.arange(6).reshape(1, 2, 3)  # ijk
B = np.arange(6).reshape(2, 3, 1)  # jlm
C = np.arange(6).reshape(3, 1, 2)  # kmn

The `np.einsum` function takes as inputs the tensors to be contracted
and a string showing the indices of each tensor and (optionally) the
indices of the output tensor.


In [ ]:
D = np.einsum("ijk, jlm, kmn -> iln", A, B, C)
print(D.shape)

# The CNOT gate

To end this section, we want to discuss a common example of a tensor
network contraction arising in quantum computing, namely the **CNOT**
gate. The [CNOT
gate](https://docs.pennylane.ai/en/stable/code/api/pennylane.CNOT.html)
can be expressed in the computational basis as

$$\mathrm{CNOT} = |0\rangle \langle 0 | \otimes I + |1\rangle \langle 1 | \otimes X.$$

That is, if the control qubit is in the $|1\rangle$ state, we apply the
$X$ gate on the target qubit; otherwise, we leave it untouched. However,
we can also rewrite this equation as a contraction. To do so, we define
two tensors:

$$\begin{aligned}
T^1 = \begin{pmatrix}
|0\rangle \langle 0|\\
|1\rangle \langle 1 |
\end{pmatrix}
\end{aligned}$$

and

$$\begin{aligned}
T^2 = \begin{pmatrix}
I \\
X
\end{pmatrix}.
\end{aligned}$$

This means $T^1_{i,j,k}$ and $T^2_{l,j,m}$ are two rank-3 tensors, where
the index $j$ *picks* the elements in the column vector while the other
two indices correspond to the indices of the internal tensors
(matrices). Specifically, the $j = 0$ element of $T^1$ and $T^2$ are
$|0\rangle \langle 0 |$ and $I$, respectively; with
$|1\rangle \langle 1|$ and $X$ for their $j = 1$ element. This means we
can redefine the CNOT expression from above as

$$\mathrm{CNOT}_{i,l,k,m} = \sum_j T^1_{i,j,k} \otimes T^2_{l,j,m} .$$

We recognize this expression as the second definition for the
contraction operation we introduced earlier. Hence, the CNOT gate can be
seen as the contraction between $T^1$ and $T^2:$

$$(\mathrm{CNOT})_{i,l,k,m} = \sum_j (T^1)_{i,j,k} (T^2)_{l,j,m}.$$

It turns out that $T^1$ and $T^2$ are special tensors known as the COPY
and XOR tensors, respectively, and therefore have special diagrammatic
representations.

![](../_static/demonstration_assets/tn_basics/07-t1-t2.png){.align-center
width="60.0%"}

Then, their contraction results in the well-known CNOT quantum circuit
representation.

![](../_static/demonstration_assets/tn_basics/08-cnot.png){.align-center
width="45.0%"}

::: note
::: title
Note
:::

By looking at the elements of the COPY tensor, we can interpret them as
being equal to $1$ when all the indices have the same value (0 or 1) and
vanishing otherwise. On the other hand, the elements of the XOR tensor
can be understood as being equal to $1$ when the values of the three
indices contain an even number of 1\'s and vanishing otherwise. We
anticipate that the COPY tensor can be used to obtain the diagonal of a
matrix. This will be useful in the last section of this demo.
:::

This demonstrates the relation between the CNOT acting as a rank-4
tensor with dimensions $2 \times 2 \times 2 \times 2$ and its
decomposition in terms of two rank-3 local tensors ($T^1$ and $T^2$) of
dimensions $2 \times 2 \times 2$.

::: note
::: title
Note
:::

More generally, we can find decompositions of multi-qubit gates into
local tensors employing the ubiquitous singular value decomposition
([SVD](https://docs.pennylane.ai/en/stable/code/api/pennylane.math.svd.html)).
This method is explained in detail in our
`introduction to matrix product states for quantum practitioners demo </demos/tutorial_mps>`{.interpreted-text
role="doc"}. This decomposition is helpful when contracting non-local
tensors, as is often required in quantum circuits.
:::


# The cost of contracting a network

A common task when dealing with tensors is the contraction of large
networks resulting in a single tensor (including scalars). To arrive at
this final tensor, we can start with a single tensor and contract it
with adjacent tensors one at a time. The order in which this is carried
out is known as the **contraction path** or **bubbling**.

While the final tensor is independent of the order of the contraction,
the number of operations performed can vary greatly depending on the
order in which we contract the intermediate tensors. Moreover, in a
general setup, finding the optimal order of indices to be contracted is
not a trivial task.

::: note
::: title
Note
:::

Actually, finding the optimal contraction path of a tensor network with
an arbitrary structure is an NP-complete problem.
:::

For this reason, in this section we will look at how to calculate the
computational cost or the **complexity** of a tensor network
contraction. First, we look at a simple matrix-matrix contraction. Given
two rank-2 tensors $G^1_{j,i}$ and $G^2_{k,j}$, we have seen that the
$(k,i)$-th element of the resulting contraction along the $j$-th index
is

$$(G^3)_{k,i} = \sum_{j=1}^{d_j} (G^2)_{k,j} (G^1)_{j,i},$$

where the indices $(i, j, k)$ have dimensions $(d_i, d_j, d_k)$,
respectively. Thus, obtaining the $(k,i)$-th element requires
$\mathcal{O}(d_j)$ operations. To construct the full tensor $G^3$, we
must repeat this procedure $d_i \times d_k$ times (once for every
possible value of $i$ and $k$). Therefore, the total complexity of the
contraction is

$$\mathcal{O}(d_i \times d_j \times d_k)$$

To illustrate the importance of choosing an efficient contraction path,
let us look at a similar contraction between three rank-3 tensors:
$A_{i,j,k} \in \mathbb{C}^{d_i \times d_j \times d_k}$,
$B_{j,l,m} \in \mathbb{C}^{d_j \times d_l \times d_m}$, and
$C_{k,m,n} \in \mathbb{C}^{d_k \times d_m \times d_n}$.

![](../_static/demonstration_assets/tn_basics/09-contraction.png){.align-center
width="50.0%"}

In particular, let us look at an example where $d_l = 1$,
$d_k = d_j = 10$, $d_m = 10^2$, and $d_n = d_i = 10^3$. First, we look
at the complexity of contracting $AB$ followed by its contraction with
$C$. As outlined in the procedure above, the first contraction results
in a complexity of

$$\sum_{j} (A)_{i,j,k} (B)_{j,l,m} \implies \mathcal{O}(d_i \times d_l \times d_m \times d_k \times d_j ) =  \mathcal{O}(d_i \times d_m \times d_j^2 ) = \mathcal{O}(10^3 10^2 (10^1)^2) = \mathcal{O}(10^7)$$

Then, contracting the resulting tensor $AB_{i, k, l, m}$ with
$C_{k,m,n}$ requires

$$\sum_{k, m} (AB)_{i, k, l, m} (C)_{k,m,n}  \implies \mathcal{O}(d_i \times d_l \times d_k \times d_m \times d_n) = \mathcal{O}(d_j \times d_m \times d_i^2) = \mathcal{O}(10^1 10^2 (10^3)^2) = \mathcal{O}(10^9)$$

operations. Since $d_j < d_m < d_i$, asymptotically, the whole
contraction will have a cost of
$\mathcal{O}(d_j \times d_m \times d_i^2) = \mathcal{O}(10^9)$.
Alternatively, we could first contract $B$ and $C$, incurring the cost

$$\sum_{m} (B)_{j,l,m} (C)_{k,m,n} \implies \mathcal{O}(d_j \times d_l \times d_m \times d_k \times d_n) = \mathcal{O}(d_i \times d_m \times d_j^2 ) = \mathcal{O}(10^3 10^2 (10^1)^2) = \mathcal{O}(10^7).$$

Then, contracting the resulting tensor with $A$ results in

$$\sum_{j, k} (A)_{i,j,k} (BC)_{j,l,k,n}  \implies  \mathcal{O}(d_j \times d_k \times d_l \times d_n \times d_i) = \mathcal{O}(d_i^2 \times d_j^2) = \mathcal{O}((10^3)^2 (10^1)^2) =\mathcal{O}(10^8).$$

This means the second contraction path results in an asymptotic cost of
$\mathcal{O}(d_i^2 \times d_j^2) = \mathcal{O}(10^8)$---lower than the
first contraction path.

To see this in practice, let us implement the above contractions using
`np.einsum`. First, we create the 3 tensors with the dimensions
specified in the example above. We demonstrate a different form of
creating tensors of the desired dimensions using the `random` module.


In [ ]:
import timeit

di = 1000
dm = 100
dj = 10

np.random.seed(20)

A = np.random.rand(di, dj, dj) # ijk
B = np.random.rand(dj,1,dm) # jlm
C = np.random.rand(dj,dm,di) # kmn

Then, we perform the individual contractions between pairs of tensors
and time them using `timeit`. We repeat the contraction `20` times and
average the computation time to account for smaller fluctuations. First,
we start by contracting $A$ and $B$.


In [ ]:
iterations = 20

contraction = "np.einsum('ijk, jlm -> iklm', A, B)"
execution_time = timeit.timeit(contraction, globals=globals(), number=iterations)

time_AB = execution_time * 1000 / iterations
print(f"Computation cost for AB contraction: {time_AB:.8f} ms")

Then, we contract the result with $C$.


In [ ]:
AB = np.einsum('ijk, jlm -> iklm', A, B)
contraction = "np.einsum('iklm, kmn -> iln', AB, C)"
execution_time = timeit.timeit(contraction, globals=globals(), number=iterations)

time_ABC = execution_time * 1000 / iterations
print(f"Computation cost for (AB)C contraction: {time_ABC:.8f} ms")

As expected, the last contraction is much more costly than the first
one. We now repeat the procedure, contracting $B$ and $C$ first.


In [ ]:
contraction = "np.einsum('jlm, kmn -> jlkn', B, C)"
execution_time = timeit.timeit(contraction, globals=globals(), number=iterations)

time_BC = execution_time * 1000 / iterations
print(f"Computation cost for BC contraction: {time_BC:.8f} ms")

We see that this contraction is of the same order of magnitude as the
contraction between $A$ and $B$, as expected from the complexity
analysis, since they both yield
$\mathcal{O}(d_i \times d_m \times d_j^2 ) = \mathcal{O}(10^7)$. Then,
we perform the contraction between the resulting tensor and $A$.


In [ ]:
BC = np.einsum('jlm, kmn -> jlkn', B, C)

contraction = "np.einsum('ijk, jlkn -> iln', A, BC)"
execution_time = timeit.timeit(contraction, globals=globals(), number=iterations)

time_BCA = execution_time * 1000 / iterations
print(f"Computation cost for A(BC) contraction: {time_BCA:.8f} ms")

We can then compare the total time for each of the paths:


In [ ]:
print(f"Computation cost for path 1: {time_AB + time_ABC}")
print(f"Computation cost for path 2: {time_BC + time_BCA}")

From this, we see that the second contraction path results in a lower
complexity compared to the first one, just as we expected! 💪


# Intermezzo

So far, we have discussed the definition of a tensor, how to combine
them to create a tensor network, and how to calculate the complexity of
the contraction operations. Hopefully, after this brief introduction,
you will feel more comfortable whenever tensor networks are brought into
the conversation.

Perhaps you even feel motivated to dive deeper into the vast world of
tensor networks!

To help you with this endeavour, in the following sections we will
summarize some ubiquitous algorithms used to connect tensor networks and
quantum computers. These topics can become quite technical real fast, so
we can only scratch the surface in this demo. For this reason, we will
reference the relevant sources when pertinent. Now, take a sip of
coffee, brace yourself, and let\'s continue! ☕️


# Connecting tensor networks and quantum circuits {#part_two}

## Contraction paths

In the previous section, we explored how the choice of the contraction
path affects the computational cost of the tensor network contraction
through a toy example. As shown in, finding an optimal contraction path
is equivalent to solving the \"multiplication problem,\" and thus, it is
in general NP-hard. In this section, we provide a general description of
the widespread techniques used to tackle this ubiquitous task.

::: note
::: title
Note
:::

In special cases, by restricting the geometry and/or the values of the
tensor networks, it is possible to find provably efficient contraction
paths. A well-studied tensor network ansatz with efficient contraction
schemes is the Matrix Product States (MPS). This section will, however,
focus on tensor networks with arbitrary structures.
:::

First, we set up the framework of the problem. While multiway
contractions---contractions between more than 2 tensors at a time---are
possible, we will consider only pairwise contractions since the former
can always be decomposed in terms of the latter. In addition,
contracting a tensor network doesn\'t need to result in a single tensor.
However, here we consider only the single tensor case as it underlies
the more general scenario.

The underlying idea behind finding a contraction path is based on the
construction of the computational graph, i.e., a rooted binary
tree---also known as the **contraction tree**---that specifies the
sequence of pairwise contractions to be executed. In this tree
structure, a leaf node corresponds to a tensor from the original network
(blue tensors) and the pairwise contractions (red lines) give rise to
the intermediate tensors (red tensors) corresponding to the rest of the
nodes in the contraction tree.

![](../_static/demonstration_assets/tn_basics/10-contraction-tree.png){.align-center
width="50.0%"}

Transforming a tensor network with an arbitrary structure into this
binary tree can be achieved by a **tree embedding** of the tensor
network graph. Thus, optimization of the contraction path is equivalent
to a search over tree embeddings of the network.

::: note
::: title
Note
:::

Besides finding a contraction path that minimizes the computational
cost, we can also attempt to find a path that optimizes the memory cost.
That is a contraction path in which all intermediate tensors are below a
certain size.
:::

Now, how do we traverse the space of trees to optimize over? The most
straightforward idea is to perform an exhaustive search through all of
them. As explained in, this can be done (with some additional
improvements) using the following well-known algorithms:

-   Depth-first search
-   Breadth-first search
-   Dynamic programming

While the exhaustive approach scales like $\mathcal{O}(N!)$, with $N$
the number of tensors in the network, it can handle a handful of tensors
within seconds, providing a good benchmark. In addition, compared to the
following algorithms, the exhaustive search guarantees finding the
global minimum and optimizing the desired metric - space and/or time.

::: note
::: title
Note
:::

A recursive implementation of the depth-first search is used by default
in the well-known package `opt_einsum` [(see
docs)](https://optimized-einsum.readthedocs.io/en/stable/optimal_path.html).
:::

Further approaches introduced in are based on alternative common
graph-theoretic tasks, rather than searching over the contraction tree
space, such as the [balanced
bi-partitioning](https://en.wikipedia.org/wiki/Balanced_number_partitioning)
and [community
detection](https://en.wikipedia.org/wiki/Community_structure)
algorithms. And even though these are only heuristics that do not
guarantee an optimal contraction path, they can often achieve an
arbitrarily close to optimal performance.

An extra level of optimization, known as **hyper-optimization**, is
introduced by the use of different algorithms to find the optimal
contraction based on the specific tensor network, as some algorithms are
better suited for certain network structures. For an in-depth
exploration of these heuristics, please refer to.

As we will explore in the next section, we can use tensor networks to
simulate quantum circuits. In particular, the calculation of an
expectation value corresponds to the contraction of the tensor network
into a single tensor (scalar). In `Pennylane`, this simulation can be
performed using the
`~pennylane.devices.default_tensor.DefaultTensor`{.interpreted-text
role="class"} device, and the method used to find the contraction path
can be chosen via the `contraction_optimizer` keyword argument.


In [ ]:
import pennylane as qml

dev = qml.device("default.tensor", method="tn", contraction_optimizer="auto-hq")

The different types of values accepted for `contraction_optimizer` are
determined by the `optimize` parameter in `Quimb` (see
[docs](https://quimb.readthedocs.io/en/latest/tensor-circuit.html#finding-a-contraction-path-the-optimize-kwarg))
as this is the backend behind the
`~pennylane.devices.default_tensor.DefaultTensor`{.interpreted-text
role="class"} device. See our [simulate quantum circuits with tensor
networks
demo](https://pennylane.ai/qml/demos/tutorial_How_to_simulate_quantum_circuits_with_tensor_networks/)
to learn more about the use of this device in `Pennylane`.

# Slicing

The size of (intermediate) tensors can grow exponentially with the
number of indices and dimensions, especially for large-scale tensor
networks. Thus, we might run into memory problems when performing the
contractions. A useful additional technique to split these tensors into
more manageable pieces is known as **slicing**.

The idea is to change space for computation time, by temporarily fixing
the values of some indices in the tensors, performing independently the
contraction for each fixed value, and summing the results.

To end this demo, let us answer the question: **how can we use tensor
networks to simulate the output of a quantum circuit?**


# Quantum circuits are tensor networks

Until now, we have looked at general tensor networks, while
✨sparkling✨ the discussions with examples related to quantum circuits.
Here, we leverage the components we have learned to explore this
relation more in-depth.

First, it is important to emphasize that quantum circuits don\'t just
\"look\" or \"behave\" like tensor networks, but rather they **are**
tensor networks! Quantum circuits are a special class of tensor networks
where each horizontal wire corresponds to the Hilbert space of a single
qubit and the tensors acting on these subsystems are restricted to be
unitary operators, denoting the time evolution of the state (from left
to right).

A general quantum circuit acting on $N$ qubits can be expressed in terms
of the initial quantum state $| \psi_0 \rangle$ and the unitary
propagator $U$ such that the evolved state is

$$| \psi \rangle = U |\psi_0 \rangle,$$

which can also be depicted diagrammatically as

![](../_static/demonstration_assets/tn_basics/11-circuit.png){.align-center
width="45.0%"}

In the right-hand side of the equality we have assumed a specific form
for the $U$ tensor in terms of local 2-qubit gates, which is often the
case when dealing with real quantum hardware. In addition, it is common
for the initial state to be a product state such as
$|0\rangle^{\otimes N}$, hence the form of the tensor in the diagram as
$N$ independent tensors of rank-1. However, an arbitrary input state is
in general represented as one big rank-$N$ tensor.

Now we can ask ourselves: what quantities can we compute from this
tensor network? 🤔

## Expectation values

As anticipated in the previous section, a natural quantity to compute
using the tensor network arising from a quantum circuit is the
expectation value of an observable $O$ evaluated at the quantum state
$|\psi \rangle$

$$\langle O \rangle = \langle \psi | O | \psi \rangle  = \langle \psi_0| U^\dagger O U |\psi_0 \rangle .$$

If the observable is a linear combination of hermitian operators (e.g.,
a Hamiltonian)

$$O = \sum_i c_i O_i ,$$

we can calculate the total expectation value \"naïvely\" by computing
the inner product for each component $O_i$ and summing up the weighted
results:

$$O = \sum_i c_i \langle O_i \rangle = \sum_i c_i \langle \psi | O_i | \psi \rangle.$$

However, it is possible to perform this operation more efficiently using
tensor networks by means of a structure called Matrix Product Operator
(MPO). The idea is to construct an efficient representation of the
observable $O$ which can be contracted with the tensor network from
$|\psi \rangle$. Constructing these networks efficiently for
Hamiltonians of arbitrary structure is an interesting task, which goes
beyond the scope of this demo.

When the observable of interest is *local*, i.e., it acts on a few
neighbouring qubits, we can calculate the expectation value by
considering only the section of the quantum circuit within the **reverse
light cone** (causal cone) of the observable $O_l$---i.e., the gates
that affect the calculation of the expectation value.

![](../_static/demonstration_assets/tn_basics/12-expectation-local.png){.align-center
width="70.0%"}

Then, the sections outside of the light cone (grayed-out gates in the
figure above) can be ignored since these are contractions resulting in
the identity: $G G^\dagger = I$. This helps us decrease the size of the
tensor to be contracted, and consequently, the computational expense, by
focusing on the section of the circuit with support inside the light
cone of the observable

$$\langle O_l \rangle = \langle \psi_l | O_l | \psi_l \rangle,$$

where $| \psi_l \rangle$ is the section of the evolved state within the
light cone of $O_l$.

## Sampling

In addition to calculating expectation values, we can also use the
tensor network arising from a quantum circuit to sample bitstrings from
the evolved probability distribution $| \psi \rangle$---emulating what
you would obtain from a real quantum computer. Since this is a
ubiquitous task in quantum information, several algorithms have been
proposed to generate samples from probability distributions represented
as tensor networks. In particular, here we discuss the \"Perfect
Sampling Algorithm\" applied to unitary tensor networks, as this
generates uncorrelated samples, unlike Markov-based approaches.

::: note
::: title
Note
:::

The method used in
[Quimb](https://quimb.readthedocs.io/en/latest/index.html) (the backend
behind
`~pennylane.devices.default_tensor.DefaultTensor`{.interpreted-text
role="class"}) to generate samples from the quantum circuit is also
based on this algorithm.
:::

A cornerstone behind this algorithm is the well-known [chain
rule](https://en.wikipedia.org/wiki/Chain_rule_(probability)), which
allows us to write the joint probability of an event using only
conditional probabilities. Using this, we can express the probability of
sampling the bitstring $(x_1, x_2, x_3, \ldots, x_N)$ from
$| \psi \rangle$ as

$$p(x_1, x_2, x_3, \ldots, x_N) = p(x_1) p(x_2|x_1) p(x_3| x_1 x_2) \ldots p(x_N | x_1 x_2 x_3 \ldots x_{N-1}).$$

Thus, to obtain a sample from the joint distribution on the left side of
the equation, we can compute the terms on the right side by means of
marginal distributions. First, we start by computing the marginal
probability $p(x_1)$. To do so, we compute the reduced density matrix
$\rho_{1}$ by tracing out all the other qubits:

$$\rho_{1} = \mathrm{Tr}_{2,3,\ldots,N}(| \psi \rangle \langle \psi |).$$

Then, the diagonal of this $2 \times 2$ density matrix gives us the
probability of sampling 0 or 1, i.e., $p(x_1 = 0)$ and $p(x_1 = 1)$.
This diagonal corresponds to the following probability vector

$$| p_{x_1} \rangle = \sum_{i=0}^{1} p(x_1=i) | i \rangle =  \mathrm{diag}(\rho_1) = \mathrm{diag}\left( \mathrm{Tr}_{2,3,\ldots,N}(| \psi \rangle \langle \psi |) \right).$$

The tensor network corresponding to the computation of this vector is

![](../_static/demonstration_assets/tn_basics/13-sample.png){.align-center
width="70.0%"}

::: note
::: title
Note
:::

In this diagram, we have extracted the diagonal of the reduced density
matrix by contracting it with the COPY tensor introduced earlier in this
demo!
:::

Once we obtain the probability vector, we can generate a random sample
weighted by these probabilities. To do so, we generate a random number
$r \in [0,1]$ and choose $x_1 = 0$ if $r < p(x_1=0)$ and $x_1 = 1$
otherwise. We save this sample as $\hat{x}_1$.

Next, we can calculate the following term $p(x_2|\hat{x}_1)$ conditioned
on the sample we have just obtained. To accomplish this, we *project*
the first qubit to be $\hat{x}_1$. We can do this by contracting the
computational basis state $| \hat{x}_1 \rangle$ with $|\psi \rangle$,
resulting in a smaller state $|\psi_{x_1} \rangle$. Then, we can proceed
exactly as we did in the previous step, calculating the reduced density
matrix $\rho_2$ by tracing out the remaining qubits $3,4,\ldots, N$ and
computing the probability vector from its diagonal

$$| p_{x_2 | \hat{x}_1} \rangle  = \mathrm{diag} \left( \mathrm{Tr}_{3,4, \ldots,N}(| \psi_{x_1} \rangle \langle \psi_{x_1} |) \right).$$

From this vector, we sample the next value $\hat{x}_2$ (just like we
sampled $\hat{x}_1$) and use it to compute the next term
$p(x_3| \hat{x}_1 \hat{x}_2)$ using the same procedure. The following
diagram shows the full tensor network for this step including the
projection onto the computational basis state $| \hat{x}_1 \rangle$.

![](../_static/demonstration_assets/tn_basics/14-sample-cntd.png){.align-center
width="70.0%"}

Analogously as done with the expectation values, these contractions only
involve the sections of the circuit within the light cone of *both* the
projection with $| \hat{x}_1 \rangle$ and the contraction with the COPY
tensor (diagonal computation). This procedure can be repeated
recursively using the chain rule equation until we obtain the full
bitstring $(\hat{x}_1, \hat{x}_2, \hat{x}_3, \ldots, \hat{x}_N)$. Then
to obtain more samples, we just repeat the procedure from the beginning!

::: note
::: title
Note
:::

By generating each bitstring independently from each other, i.e., by
restarting the sampling algorithm without knowledge of the previous
samples, we ensure perfect sampling from the probability distribution,
contrary to other Markov-based algorithms . We then say the sample is
*memoryless*.
:::

We can reduce the computational cost of the sampling algorithm by
**caching** results from previous contractions. When we draw a new
sample that partially matches a previously explored configuration
(marginal probability), we can reuse the cached results and avoid
contracting this part of the network over again.

For example, let\'s assume we have performed the perfect sampling
algorithm once and obtained the sample $0110$. If the next sample we
need to generate starts with the substring $01$, we can reuse the
marginal probabilities up to $p(x_3|01)$ and only calculate the new
parts of the sequence. The same caching idea can be applied to other
tensor network algorithms involving many contractions.


# Conclusion

And that is it for this demo! 🎉

Although the world of tensor networks and their relation to quantum
computing is vastly wider than what we could ever cover in one demo, we
hope that after these explanations you now feel equipped with the tools
needed to dive deeper into this topic by yourself.

If you want to learn more about using tensor networks as a diagrammatic
tool, check out these amazing [lecture notes on quantum tensor
networks](https://arxiv.org/pdf/1912.10049) by J.Biamonte. In addition,
check out the [Tensor Network website](https://tensornetwork.org/about/)
for great explanations on many important algorithms and tensor network
structures by Flatiron Institute.


# References


# About the author
